In [1]:
import os
import pandas as pd
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json
import urllib.request
import time
import bs4 as bs
# from geopy.geocoders import Nominatim
import geopandas as gpd
import seaborn as sns
import ast
import folium
from tqdm import tqdm
# from shapely.geometry import mapping
# import branca.colormap as cm

In [2]:
total_pages = 200 #currently max 200 pages
links = []

for page in tqdm(range(1,(total_pages + 1))):
    # if page%10 == 0:
    #     print(page)
    user_agent = 'Mozilla/5.0 (Windows; U; Windows NT 5.1; en-US; rv:1.9.0.7) Gecko/2009021910 Firefox/3.0.7'
    url = f"https://www.zoocasa.com/toronto-on-real-estate/sold?page={page}"
    # url = f"https://www.zolo.ca/toronto-real-estate/sold/page-{page}?"
    headers={'User-Agent':user_agent,}
    request=urllib.request.Request(url,None,headers) #The assembled request
    #request = urllib.request.Request(url)
    data_raw = urllib.request.urlopen(request).read()
    soup = bs.BeautifulSoup(data_raw, 'lxml')

    desc = soup.find_all("script",id="__NEXT_DATA__")
    json_data = json.loads(desc[0].contents[0])
    data_ls = json_data['props']['pageProps']['props']['viewModel']['listingsData']
    for i in range(len(data_ls)):
        try:
            links.append(data_ls[i]['address_url_absolute_path'])
        except:
            print(f'Link {i} on page {page} not read.')

    # # zolo
    # link_ls = soup.find_all(attrs={'class':'address text-primary'})
    # for i in range(len(link_ls)):
    #     try:
    #         links.append(link_ls[i]['href'])
    #     except:
    #         print(f'Link {i} on page {page} not read.')
    
with open('house_links.txt', 'w') as file:
    for item in links:
        file.write(f"{item}\n")

100%|██████████| 200/200 [01:49<00:00,  1.82it/s]


In [3]:
# Prepare a table for data population
with open('house_links.txt', 'r') as file:
    links = [line.strip() for line in file]
user_agent = 'Mozilla/5.0 (Windows; U; Windows NT 5.1; en-US; rv:1.9.0.7) Gecko/2009021910 Firefox/3.0.7'
headers={'User-Agent':user_agent,}

In [4]:
# # url = 'https://www.zoocasa.com' + str(links[0])
# url = 'https://www.zoocasa.com' + "/toronto-on-real-estate/king-parliament/908-60-tannery-rd"

# #read data, convert to 2 formats
# request=urllib.request.Request(url,None,headers) #The assembled request
# data_raw = urllib.request.urlopen(request).read()
# soup = bs.BeautifulSoup(data_raw, 'lxml')
# print(soup.prettify())
# desc = soup.find_all("script",id="__NEXT_DATA__")
# json_data = json.loads(desc[0].contents[0])
# info_dict = json_data['props']['pageProps']['props']['listingsData'][0]
# info_dict

In [4]:
start_time = time.time()
skipped = []
url_list=[]
json_list=[]

for no in tqdm(range(len(links))):
    try:
        url = 'https://www.zoocasa.com' + str(links[no])

        #read data, convert to 2 formats
        request=urllib.request.Request(url,None,headers) #The assembled request
        data_raw = urllib.request.urlopen(request).read()
        soup = bs.BeautifulSoup(data_raw, 'lxml')

        desc = soup.find_all("script",id="__NEXT_DATA__")
        json_data = json.loads(desc[0].contents[0])

        info_dict = json_data['props']['pageProps']['props']['listingsData'][0]['attributes']

        url_list.append(url)
        json_list.append(info_dict)
        
        #pause and print
        # time.sleep(1)
        # if no % 100 == 0: print(no, 'is done')
    
    except: 
        print('Problem with: ', no)
        skipped.append(no)
        continue

 13%|█▎        | 712/5400 [07:01<46:11,  1.69it/s]  

Problem with:  711


 29%|██▉       | 1582/5400 [15:20<35:13,  1.81it/s]

Problem with:  1581


100%|██████████| 5400/5400 [52:29<00:00,  1.71it/s]


In [5]:
print('Skipped: ', skipped, ', Total: ', len(skipped))
print('Total time: %.2f' % (time.time() - start_time))

housing_df = pd.json_normalize(json_list)
print(f'housing categories : {housing_df.columns}')
housing_df['url']=url_list
housing_df.head()

Skipped:  [711, 1581] , Total:  2
Total time: 3149.21
housing categories : Index(['is-rental', 'status', 'price', 'square-footage', 'address-path',
       'bedrooms', 'bathrooms', 'bedrooms-partial', 'bathrooms-partial',
       'parking',
       ...
       'image-descs.39', 'image-descs.40', 'image-descs.41', 'image-descs.42',
       'image-descs.43', 'image-descs.44', 'image-descs.45', 'image-descs.46',
       'image-descs.47', 'image-descs.48'],
      dtype='object', length=170)


is-rental              status      price  square-footage  \
0      False  not_available_sold  1475000.0             NaN   
1      False  not_available_sold  2650000.0             NaN   
2      False  not_available_sold  1850000.0             NaN   
3      False  not_available_sold   795000.0             NaN   
4      False  not_available_sold  2695000.0             NaN   

                                        address-path  bedrooms  bathrooms  \
0  /toronto-on-real-estate/yorkville/206-55-scoll...         1          1   
1  /toronto-on-real-estate/deer-park/203-70-roseh...         2          3   
2  /toronto-on-real-estate/yorkville/202-181-dave...         1          2   
3  /toronto-on-real-estate/agincourt-north/74-70-...         3          2   
4  /toronto-on-real-estate/south-hill/th-8-260-ru...         3          5   

   bedrooms-partial  bathrooms-partial parking  ...  image-descs.39  \
0               NaN                NaN       1  ...             NaN   
1               NaN                NaN       2  ...             NaN   
2               NaN                NaN       1  ...             NaN   
3               NaN                NaN       2  ...             NaN   
4               NaN                NaN       2  ...             NaN   

   image-descs.40  image-descs.41  image-descs.42 image-descs.43  \
0             NaN             NaN             NaN            NaN   
1             NaN             NaN             NaN            NaN   
2             NaN             NaN             NaN            NaN   
3             NaN             NaN             NaN            NaN   
4             NaN             NaN             NaN            NaN   

  image-descs.44 image-descs.45 image-descs.46 image-descs.47 image-descs.48  
0            NaN            NaN            NaN            NaN            NaN  
1            NaN            NaN            NaN            NaN            NaN  
2            NaN            NaN            NaN            NaN            NaN  
3            NaN            NaN            NaN            NaN            NaN  
4            NaN            NaN            NaN            NaN            NaN  

[5 rows x 170 columns]

In [6]:
print(housing_df.shape)

(5398, 170)


In [7]:
housing_df['type'].value_counts()

type
Condo Apt                  3052
Detached                    685
Semi-Detached               632
Condo Townhouse             285
Apartment/Condominium       272
Att/Row/Twnhouse            197
Comm Element Condo           68
Single Family Residence      54
Attached                     32
Duplex                       28
Condominium                  27
Triplex                      17
Co-Op Apt                    17
Co-Ownership Apt             17
Multiplex                     4
Apartment                     3
Parking Space                 2
Semi Detached                 2
Multi-Family                  2
Fourplex                      1
Other                         1
Name: count, dtype: int64

In [10]:

housing_df.dropna(subset=['sold-price'], inplace=True)
print(housing_df.shape)
# housing_df.drop_duplicates(inplace=True)
# print(housing_df.shape)

(5183, 170)


In [11]:
## Identify missing values
no_loc = housing_df['position.coordinates'].isnull().sum()
print(f'houses with no known coordinate: {no_loc}')
housing_df.describe()

houses with no known coordinate: 0


square-footage     bedrooms    bathrooms  bedrooms-partial  \
count             0.0  5183.000000  5183.000000       2192.000000   
mean              NaN     2.090488     1.992861          1.056113   
std               NaN     1.165283     1.097235          0.337858   
min               NaN     0.000000     0.000000          0.000000   
25%               NaN     1.000000     1.000000          1.000000   
50%               NaN     2.000000     2.000000          1.000000   
75%               NaN     3.000000     2.000000          1.000000   
max               NaN     9.000000    14.000000          8.000000   

       bathrooms-partial   provider-id  image-descs  maintenance-fees  \
count          20.000000   5183.000000          0.0       3383.000000   
mean            0.050000  30004.858962          NaN        743.286329   
std             0.223607     62.752286          NaN        492.705757   
min             0.000000  30000.000000          NaN          0.000000   
25%             0.000000  30001.000000          NaN        483.575000   
50%             0.000000  30001.000000          NaN        623.300000   
75%             0.000000  30001.000000          NaN        831.705000   
max             1.000000  31013.000000          NaN      10017.000000   

              taxes  square-footage.max  square-footage.min  
count   4802.000000         3998.000000         3963.000000  
mean    4659.617834         1139.481241          916.855917  
std     3592.776673          768.934881          607.768575  
min        0.000000          499.000000            0.000000  
25%     2530.000000          699.000000          600.000000  
50%     3534.950000          799.000000          700.000000  
75%     5563.390000         1399.000000         1100.000000  
max    53190.910000         5000.000000         4750.000000

In [12]:
total_count = housing_df.shape[0]
drop_cols = [col_name for col_name in housing_df.columns.to_list() if housing_df[col_name].isnull().sum()==total_count]
drop_cols

['square-footage',
 'image-descs',
 'listing-agent',
 'listing-agent-phone',
 'original-mls-name']

In [13]:
housing_df.drop(columns=drop_cols).to_csv('houses_all_data.csv')

### Read in Housing CSV

In [15]:
housing_df = pd.read_csv('houses_all_data.csv', index_col='Unnamed: 0')
housing_df.drop_duplicates(inplace=True)
print(housing_df.shape)
housing_df['position.coordinates'] = housing_df['position.coordinates'].apply(ast.literal_eval)
housing_df.head()

C:\Users\stdon\AppData\Local\Temp\ipykernel_22480\2405502663.py:1: DtypeWarning: Columns (31,62,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165) have mixed types. Specify dtype option on import or set low_memory=False.
  housing_df = pd.read_csv('houses_all_data.csv', index_col='Unnamed: 0')


(5142, 165)


is-rental              status      price  \
0      False  not_available_sold  1475000.0   
1      False  not_available_sold  2650000.0   
2      False  not_available_sold  1850000.0   
3      False  not_available_sold   795000.0   
4      False  not_available_sold  2695000.0   

                                        address-path  bedrooms  bathrooms  \
0  /toronto-on-real-estate/yorkville/206-55-scoll...         1          1   
1  /toronto-on-real-estate/deer-park/203-70-roseh...         2          3   
2  /toronto-on-real-estate/yorkville/202-181-dave...         1          2   
3  /toronto-on-real-estate/agincourt-north/74-70-...         3          2   
4  /toronto-on-real-estate/south-hill/th-8-260-ru...         3          5   

   bedrooms-partial  bathrooms-partial  parking  is-vow  ...  image-descs.39  \
0               NaN                NaN      1.0    True  ...             NaN   
1               NaN                NaN      2.0    True  ...             NaN   
2               NaN                NaN      1.0    True  ...             NaN   
3               NaN                NaN      2.0    True  ...             NaN   
4               NaN                NaN      2.0    True  ...             NaN   

   image-descs.40  image-descs.41 image-descs.42 image-descs.43  \
0             NaN             NaN            NaN            NaN   
1             NaN             NaN            NaN            NaN   
2             NaN             NaN            NaN            NaN   
3             NaN             NaN            NaN            NaN   
4             NaN             NaN            NaN            NaN   

  image-descs.44 image-descs.45 image-descs.46 image-descs.47 image-descs.48  
0            NaN            NaN            NaN            NaN            NaN  
1            NaN            NaN            NaN            NaN            NaN  
2            NaN            NaN            NaN            NaN            NaN  
3            NaN            NaN            NaN            NaN            NaN  
4            NaN            NaN            NaN            NaN            NaN  

[5 rows x 165 columns]

In [34]:

housing_df['geometry'] = gpd.points_from_xy(pd.DataFrame(housing_df["position.coordinates"].to_list())[0],
                                            pd.DataFrame(housing_df["position.coordinates"].to_list())[1])

In [35]:
housing_gdf = gpd.GeoDataFrame(housing_df, geometry='geometry', crs='epsg:4326')
housing_gdf['geometry']

148     POINT (-79.35485 43.65331)
149     POINT (-79.55900 43.60926)
150     POINT (-79.40629 43.64862)
151     POINT (-79.39546 43.65849)
152     POINT (-79.37568 43.66790)
                   ...            
5390    POINT (-79.39887 43.67950)
5391    POINT (-79.41858 43.67126)
5392    POINT (-79.38212 43.65697)
5393    POINT (-79.37894 43.65461)
5394    POINT (-79.40159 43.63448)
Name: geometry, Length: 5044, dtype: geometry

In [36]:
# # # what happens if I skip this
# housing_gdf['projected_geometry']=housing_gdf['geometry'].to_crs('EPSG:26919')

In [37]:
condo_types = ['Condo Apt','Comm Element Condo','Co-Op Apt','Co-Ownership Apt']
condo_gdf = housing_gdf[housing_gdf['type'].str.strip().isin(condo_types)]
house_gdf = housing_gdf[~housing_gdf['type'].str.strip().isin(condo_types)]

In [38]:
house_gdf.shape

(2020, 165)

### Neighbourhood level analysis

In [18]:
#get Toronto neighbourhood profiles
hood_data = pd.read_csv('C:/Users/stdon/Documents/Toronto-housing-price-prediction/opendata_neighbourhoods/neighbourhood-profiles-2016-csv.csv')
hood_data[hood_data.columns[4:]].head()
hood_data = hood_data[hood_data.columns[4:]].T.reset_index()
new_header = hood_data.iloc[0] #grab the first row for the header
hood_data = hood_data[1:] #take the data less the header row
hood_data.columns = new_header #set the header row as the df header
hood_data.head()

0                Characteristic Neighbourhood Number TSNS2020 Designation  \
1               City of Toronto                  NaN                  NaN   
2               Agincourt North                  129       No Designation   
3  Agincourt South-Malvern West                  128       No Designation   
4                     Alderwood                   20       No Designation   
5                         Annex                   95       No Designation   

0 Population, 2016 Population, 2011 Population Change 2011-2016  \
1        2,731,571        2,615,060                       4.50%   
2           29,113           30,279                      -3.90%   
3           23,757           21,988                       8.00%   
4           12,054           11,904                       1.30%   
5           30,526           29,177                       4.60%   

0 Total private dwellings Private dwellings occupied by usual residents  \
1               1,179,057                                     1,112,929   
2                   9,371                                         9,120   
3                   8,535                                         8,136   
4                   4,732                                         4,616   
5                  18,109                                        15,934   

0 Population density per square kilometre Land area in square kilometres  ...  \
1                                   4,334                          630.2  ...   
2                                   3,929                           7.41  ...   
3                                   3,034                           7.83  ...   
4                                   2,435                           4.95  ...   
5                                  10,863                           2.81  ...   

0       External migrants  \
1                  59,945   
2                     605   
3                     490   
4                      70   
5                     835   

0 Total - Mobility status 5 years ago - 25% sample data   Non-movers  \
1                                          2,556,120       1,516,110   
2                                             27,490          18,865   
3                                             22,325          13,565   
4                                             11,370           8,235   
5                                             27,715          12,980   

0     Movers     Non-migrants     Migrants       Internal migrants  \
1  1,040,015          639,060      400,950                 184,120   
2      8,610            5,445        3,170                     880   
3      8,775            5,610        3,145                     980   
4      3,130            2,200          925                     680   
5     14,735            8,340        6,390                   3,930   

0         Intraprovincial migrants         Interprovincial migrants  \
1                          141,135                           42,985   
2                              735                              135   
3                              760                              220   
4                              615                               70   
5                            2,630                            1,310   

0       External migrants  
1                 216,835  
2                   2,280  
3                   2,170  
4                     245  
5                   2,460  

[5 rows x 2384 columns]

In [31]:
# Create a Folium map centered on the mean of the GeoPandas DataFrame
hood_geodata = gpd.read_file('C:/Users/stdon/Documents/Toronto-housing-price-prediction/opendata_neighbourhoods/Neighbourhoods.shp')
# rename columns
hood_geodata_columns = pd.read_csv('C:/Users/stdon/Documents/Toronto-housing-price-prediction/opendata_neighbourhoods/Neighbourhoods_fields.csv')
hood_geodata.columns = hood_geodata_columns.name.values

hood_geodata_map = hood_geodata.to_crs('EPSG:4326')
hood_geodata_project = hood_geodata.to_crs('EPSG:26919')
#hood_geodata['geometry'] = hood_geodata['geometry'].to_crs('EPSG:4269')
#hood_geodata['projected_geometry'] = hood_geodata['geometry'].to_crs('EPSG:26919')

m = folium.Map(location=[hood_geodata_map.geometry.centroid.y.mean(), hood_geodata_map.geometry.centroid.x.mean()], zoom_start=10)

# Add the GeoPandas DataFrame to the map
folium.GeoJson(hood_geodata_map).add_to(m)

m

C:\Users\stdon\AppData\Local\Temp\ipykernel_12668\1162143137.py:12: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[hood_geodata_map.geometry.centroid.y.mean(), hood_geodata_map.geometry.centroid.x.mean()], zoom_start=10)


In [9]:
hood_geodata_map.shape

(140, 16)

In [39]:
### 
house_hood_gdf = gpd.sjoin(house_gdf, hood_geodata_map[['_id','AREA_NAME','geometry']], how='right', predicate='within')
print(house_hood_gdf.shape)
house_hood_gdf.head(3)

(2028, 168)


index_left is-rental              status      price  \
0      1948.0     False  not_available_sold  1189000.0   
0      2163.0     False  not_available_sold  1389000.0   
0       673.0     False  not_available_sold  1049000.0   

                                        address-path  bedrooms  bathrooms  \
0  /toronto-on-real-estate/dufferin-davenport/113...       6.0        2.0   
0  /toronto-on-real-estate/wychwood-park/13-acore...       3.0        2.0   
0  /toronto-on-real-estate/wychwood-park/47-march...       3.0        2.0   

   bedrooms-partial  bathrooms-partial  parking  ... image-descs.42  \
0               NaN                NaN      2.0  ...            NaN   
0               1.0                NaN      1.0  ...            NaN   
0               NaN                NaN      1.0  ...            NaN   

  image-descs.43 image-descs.44 image-descs.45 image-descs.46 image-descs.47  \
0            NaN            NaN            NaN            NaN            NaN   
0            NaN            NaN            NaN            NaN            NaN   
0            NaN            NaN            NaN            NaN            NaN   

  image-descs.48  _id      AREA_NAME  \
0            NaN  141  Wychwood (94)   
0            NaN  141  Wychwood (94)   
0            NaN  141  Wychwood (94)   

                                            geometry  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...  

[3 rows x 168 columns]

In [12]:
print(house_hood_gdf.columns.to_list())

['index_left', 'id', 'price', 'soldPrice', 'bedrooms', 'bedroomsPartial', 'bathrooms', 'bathroomsPartial', 'isVow', 'isCrea', 'isItsoVow', 'isRental', 'unitNumber', 'streetNumber', 'streetName', 'neighbourhoodName', 'city', 'imageUrl', 'thumbnailUrl', 'imageDesc', 'addedAt', 'expiredAt', 'soldAt', 'path', 'province', 'addressPath', 'status', 'lastStatus', 'isImageReady', 'addressSlug', 'availableAt', 'mlsNum', 'postalCode', 'imageUrls', 'thumbnailUrls', 'virtualTourUrl', 'description', 'brokerage', 'disclaimer', 'type', 'levels', 'locker', 'parking', 'maintenanceFees', 'taxes', 'exterior', 'basement', 'garage', 'driveway', 'heat', 'ac', 'heatingFuel', 'rooms', 'extras', 'openHouses', 'lotFrontage', 'lotDepth', 'style', 'styleName', 'url', 'position.type', 'position.coordinates', 'neighbourhood.id', 'misc.approxAge', 'misc.balcony', 'misc.bldgAmenities1Out', 'misc.bldgAmenities2Out', 'misc.bldgAmenities3Out', 'misc.bldgAmenities4Out', 'misc.bldgAmenities5Out', 'misc.bldgAmenities6Out', 

In [41]:
price_by_hood = house_hood_gdf.groupby(['_id','AREA_NAME'], as_index=False)['sold-price'].mean().sort_values('sold-price').round(0)
display(price_by_hood)

_id                      AREA_NAME  sold-price
12   153                  Malvern (132)    643767.0
105  246              Dorset Park (126)    655000.0
104  245        Don Valley Village (47)    732500.0
111  252            Eglinton East (138)    750998.0
35   176      Pelmo Park-Humberlea (23)    769469.0
..   ...                            ...         ...
57   198          Thorncliffe Park (55)         NaN
84   225  Beechborough-Greenbrook (112)         NaN
96   237   Centennial Scarborough (133)         NaN
115  256       Etobicoke West Mall (13)         NaN
116  257           Flemingdon Park (44)         NaN

[140 rows x 3 columns]

In [44]:
mean_val = price_by_hood['sold-price'].mean()
hood_price_gdf = hood_geodata_map.merge(price_by_hood.fillna(mean_val), on=['_id','AREA_NAME'], how='left')

In [45]:
hood_price_gdf.head(3)

_id   AREA_ID  AREA_ATTR_ID  PARENT_AREA_ID  AREA_SHORT_CODE  \
0  141  25886861      25926662           49885               94   
1  142  25886820      25926663           49885              100   
2  143  25886834      25926664           49885               97   

   AREA_LONG_CODE             AREA_NAME             AREA_DESC     X     Y  \
0              94         Wychwood (94)         Wychwood (94)  None  None   
1             100  Yonge-Eglinton (100)  Yonge-Eglinton (100)  None  None   
2              97   Yonge-St.Clair (97)   Yonge-St.Clair (97)  None  None   

   LONGITUDE   LATITUDE  OBJECTID   Shape__Area  Shape__Length  \
0 -79.425515  43.676919  16491505  3.217960e+06    7515.779658   
1 -79.403590  43.704689  16491521  3.160334e+06    7872.021074   
2 -79.397871  43.687859  16491537  2.222464e+06    8130.411276   

                                            geometry  sold-price  
0  POLYGON ((-79.43592 43.68015, -79.43492 43.680...   1682038.0  
1  POLYGON ((-79.41096 43.70408, -79.40962 43.704...   2364538.0  
2  POLYGON ((-79.39119 43.68108, -79.39141 43.680...   3376676.0

In [46]:

# # m = folium.Map(location=[43.651, -79.347], zoom_start=10)
# m = folium.Map(location=[hood_price_gdf.geometry.centroid.y.mean(), hood_price_gdf.geometry.centroid.x.mean()], zoom_start=11)

# # prices = folium.FeatureGroup(name='Neighbourhood Prices')

# choropleth = folium.Choropleth(
#     geo_data=hood_price_gdf,
#     name="neighbourhood prices",
#     data=hood_price_gdf,
#     columns=['AREA_NAME',"soldPrice"],
#     key_on="feature.properties.AREA_NAME",
#     fill_color="YlOrRd",
#     bins = [hood_price_gdf['soldPrice'].min(),800000, 900000,1000000,1100000, 1200000, 1500000, 2000000, \
#             hood_price_gdf['soldPrice'].max()],
#     fill_opacity=0.7,
#     line_opacity=0.2,
#     legend_name="Price",
#     highlight=True
# ).add_to(m)

# tooltip = folium.GeoJsonTooltip(
#     fields=['AREA_NAME', 'soldPrice'],
#     aliases=['Name:', 'Price:'],
#     localize=True,
#     sticky=False,
#     labels=True,
#     style="""
#         background-color: #F0EFEF;
#         border: 2px solid black;
#         border-radius: 3px;
#         box-shadow: 3px;
#     """
# )
# # Add the tooltip to the choropleth map layer
# choropleth.geojson.add_child(tooltip)
# # 

# # folium.LayerControl().add_to(m)

# ### Todo: delete legend - not helpful

# m

In [47]:
# m.save('E:/Toronto-housing-price-prediction/opendata_neighbourhoods/price_map.html')

### Public Transit

Average prices around major stations

In [49]:
#list of existing, constructing, and proposed train lines
train_line_path='C:/Users/stdon/Documents/Toronto-housing-price-prediction/FRTN_TRANSIT_NETWORK/FRTN_TRANSIT_NETWORK.shp'
train_station_path='C:/Users/stdon/Documents/Toronto-housing-price-prediction/FRTN_TRANSIT_NETWORK/FRTN_POINTS.shp'

line_geodata = gpd.read_file(train_line_path)
station_geodata = gpd.read_file(train_station_path)

#filter only for existing or under construction
real_lines = ['Sheppard Subway','Yonge-University-Spadina Subway','Spadina Subway Extension','Bloor Subway',
              'Eglinton West LRT','Scarborough Subway','Ontario Line','Eglinton Crosstown LRT','Finch West LRT']
real_stations = ['Yonge-University Subway', 'Bloor-Danforth Subway', 'Eglinton Crosstown LRT', 'Finch West LRT','Ontario Line',
                'Eglinton West LRT','Toronto-York Spadina Subway Extension','Sheppard Subway','Scarborough Subway']
train_lines = line_geodata[line_geodata['NAME'].isin(real_lines)]
train_stations = station_geodata[station_geodata['NAME'].isin(real_stations)]

#line_geodata['colors'] = ['gold','limegreen', 'plum']

train_lines['geometry'] = train_lines['geometry'].to_crs('EPSG:4326')
train_stations['geometry'] = train_stations['geometry'].to_crs('EPSG:4326')

train_lines['projected_geometry'] = train_lines['geometry'].to_crs('EPSG:26919')
train_stations['projected_geometry'] = train_stations['geometry'].to_crs('EPSG:26919')

c:\Users\stdon\anaconda3\Lib\site-packages\geopandas\geodataframe.py:1528: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\stdon\anaconda3\Lib\site-packages\geopandas\geodataframe.py:1528: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\stdon\anaconda3\Lib\site-packages\geopandas\geodataframe.py:1528: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer]

In [50]:
## There are a few repeats/transfer stations
dup_list = ['Sheppard-Yonge','Eglinton','Bloor-Yonge','Queen','Osgoode','St. George','Spadina','Sheppard West','Kennedy','Pape', 'Science Centre']
dup_stations = train_stations[train_stations['LOCATION_N'].isin(dup_list)] #same as eglinton west
no_dup_stations = train_stations[~train_stations['LOCATION_N'].isin(dup_list)]
drop_list = ['Cedarvale','Mt Dennis'] #these names are repeated except for minor spelling variations
train_stations = pd.concat([no_dup_stations[~no_dup_stations['LOCATION_N'].isin(drop_list)], dup_stations.drop_duplicates(subset='LOCATION_N')])
print(train_stations['LOCATION_N'].to_list())

['Avenue', 'Forest Hill', 'Leaside', 'Sloane', 'Birchmount', 'Caledonia', 'Chaplin', 'Fairbank', 'Aga Khan Park & Museum', 'Ionview', 'Keelesdale', 'Laird', 'Hakimi Lebovic', 'Sunnybrook Park', 'Mount Dennis', 'Mount Pleasant', 'Oakwood', 'Pharmacy', "O'Connor", 'Golden Mile', 'Wynford', 'Kipling', 'Islington', 'Royal York', 'Old Mill', 'Jane', 'Runnymede', 'High Park', 'Keele', 'Dundas West', 'Lansdowne', 'Dufferin', 'Ossington', 'Christie', 'Bathurst', 'Bay', 'Sherbourne', 'Castle Frank', 'Broadview', 'Chester', 'Donlands', 'Greenwood', 'Coxwell', 'Woodbine', 'Main Street', 'Victoria Park', 'Warden', 'Union', 'St. Andrew', 'King', 'St. Patrick', 'Dundas', "Queen's Park", 'College', 'Wellesley', 'Museum', 'Rosedale', 'Summerhill', 'St. Clair', 'Davisville', 'Lawrence', 'York Mills', 'North York Centre', 'Finch', 'Dupont', 'St Clair West', 'Eglinton West', 'Glencairn', 'Lawrence West', 'Yorkdale', 'Wilson', 'Bayview', 'Bessarion', 'Leslie', 'Don Mills', 'Downsview Park', 'Finch West', 

In [51]:
housing_gdf[housing_gdf['geometry'].to_crs('EPSG:26919').distance(train_stations['projected_geometry'].iloc[100]) < 2000].shape
## After playing around, this value seems closest to google maps values

(7, 165)

In [52]:
# housing_gdf['projected_geometry']=housing_gdf['geometry'].to_crs('EPSG:26919')

In [63]:
housing_gdf['type'].value_counts(dropna=False)

Condo Apt             4334
Detached              2287
Semi-Detached          860
Condo Townhouse        477
Att/Row/Twnhouse       280
Comm Element Condo     116
Co-Op Apt               40
Duplex                  21
Triplex                 19
Co-Ownership Apt        18
Attached                12
Multiplex               10
Link                     5
Store W/Apt/Offc         4
Other                    2
Fourplex                 2
Lower Level              1
Parking Space            1
Name: type, dtype: int64

In [16]:
# condo_types = ['Condo Apt','Comm Element Condo','Co-Op Apt','Co-Ownership Apt']
# condo_gdf = housing_gdf[housing_gdf['type'].str.strip().isin(condo_types)]
# house_gdf = housing_gdf[~housing_gdf['type'].str.strip().isin(condo_types)]

#### Note I am doing this for houses only

In [54]:
house_gdf['projected_geometry']=house_gdf['geometry'].to_crs('EPSG:26919')
sold_count=[]
sold_amt=[]
station_names = []

for index in range(train_stations.shape[0]):
    station_info = train_stations.iloc[index]
    station = station_info['LOCATION_N']
    station_names.append(station)
    close_houses = house_gdf[house_gdf['projected_geometry'].distance(station_info['projected_geometry']) < 2000]
    sold_count.append(close_houses.shape[0])
    sold_amt.append(close_houses['sold-price'].mean())
    print(f'Analyzed station: {station}')
    
transit_stats = pd.DataFrame({'station':station_names, 'mean sold price':sold_amt, 'sold number': sold_count})

c:\Users\stdon\anaconda3\Lib\site-packages\geopandas\geodataframe.py:1528: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


Analyzed station: Avenue
Analyzed station: Forest Hill
Analyzed station: Leaside
Analyzed station: Sloane
Analyzed station: Birchmount
Analyzed station: Caledonia
Analyzed station: Chaplin
Analyzed station: Fairbank
Analyzed station: Aga Khan Park & Museum
Analyzed station: Ionview
Analyzed station: Keelesdale
Analyzed station: Laird
Analyzed station: Hakimi Lebovic
Analyzed station: Sunnybrook Park
Analyzed station: Mount Dennis
Analyzed station: Mount Pleasant
Analyzed station: Oakwood
Analyzed station: Pharmacy
Analyzed station: O'Connor
Analyzed station: Golden Mile
Analyzed station: Wynford
Analyzed station: Kipling
Analyzed station: Islington
Analyzed station: Royal York
Analyzed station: Old Mill
Analyzed station: Jane
Analyzed station: Runnymede
Analyzed station: High Park
Analyzed station: Keele
Analyzed station: Dundas West
Analyzed station: Lansdowne
Analyzed station: Dufferin
Analyzed station: Ossington
Analyzed station: Christie
Analyzed station: Bathurst
Analyzed station:

In [55]:
station_house_stats = transit_stats.sort_values('mean sold price')
station_house_stats['mean sold price'] = round(station_house_stats['mean sold price'],-2)
station_house_stats.head(20) #Cheapest subway stations

station  mean sold price  sold number
77    York University         620000.0            1
79        Highway 407         620000.0            1
78    Pioneer Village         825000.0            2
86          Stevenson         847700.0            6
95               Jane         864900.0            5
98           Sentinel         873400.0            5
87            Kipling         874000.0            9
14       Mount Dennis         879200.0           11
96          Driftwood         893200.0            6
97          Tobermory         893200.0            6
94   Norfinch/Oakdale         907200.0            9
92             Weston         911800.0           10
91      Milvan/Rumike         922700.0            9
93       Signet/Arrow         927600.0            8
74          Don Mills         950800.0            6
88          Islington         954000.0           12
100              Jane         965600.0            5
83           Westmore         965900.0            9
85             Albion         968500.0            6
127           Kennedy         979000.0           10

In [56]:
### Scale the results by the distance from downtown
## Define as the location of 
train_stations_houses = train_stations.merge(station_house_stats, how='inner',left_on='LOCATION_N', right_on='station')


In [57]:
from shapely.geometry import Point
city_hall = Point(-79.383889,43.653333)
city_hall_df = gpd.GeoDataFrame({'geometry': [city_hall]}, crs='EPSG:4326')
train_stations_houses['dist2dt']=train_stations_houses['projected_geometry'].distance(city_hall_df['geometry'].to_crs('EPSG:26919').iloc[0])

In [58]:

# m = folium.Map(location=[43.651, -79.347], zoom_start=10)
m2 = folium.Map(location=[hood_price_gdf.geometry.centroid.y.mean(), hood_price_gdf.geometry.centroid.x.mean()], zoom_start=11)

choropleth = folium.Choropleth(
    geo_data=hood_price_gdf,
    name="neighbourhood prices",
    data=hood_price_gdf,
    columns=['AREA_NAME',"sold-price"],
    key_on="feature.properties.AREA_NAME",
    fill_color="YlOrRd",
    bins = [hood_price_gdf['sold-price'].min(),800000, 900000,1000000,1100000, 1200000, 1500000, 2000000, \
            hood_price_gdf['sold-price'].max()],
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Price",
    highlight=True
).add_to(m2)

tooltip = folium.GeoJsonTooltip(
    fields=['AREA_NAME', 'sold-price'],
    aliases=['Name:', 'Price:'],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """
)
# Add the tooltip to the choropleth map layer
choropleth.geojson.add_child(tooltip)


# subway_colors = {'Sheppard Subway':'#B00085', 'Yonge-University-Spadina Subway':'#F3EB00',
#        'Spadina Subway Extension':'#F3EB00', 'Eglinton Crosstown LRT':'#F39E00',
#        'Eglinton West LRT':'#F39E00', 'Scarborough Subway':'#21A900', 'Finch West LRT':'#949793',
#        'Bloor Subway':'#21A900', 'Ontario Line':'#009CD7'}

transit = folium.FeatureGroup(name='transit',overlay=True,show=True)

subway_line = folium.features.GeoJson(train_lines['geometry'], name='subway',
                                        style_function = lambda x: {'color': 'black'
                                                                    ,'weight': 2})
# m2.add_child(subway_line)
subway_line.add_to(transit)

# for index, row in train_lines.iterrows():
#     # Extract the LineString geometry
#     curve = row['geometry']

#     # Create a PolyLine and add it to the map
#     if curve.type =='LineString':
#         folium.PolyLine(locations=curve.coords, color='blue', weight=10).add_to(m2)
#     else:
#         for line in curve:
#             folium.PolyLine(locations=line.coords, color='blue', weight=10).add_to(m2)
# #     else:
# #         print('not a line, cannot draw')

# Iterate over the rows of the GeoDataFrame
for index, row in train_stations_houses.iterrows():
    # Get the coordinates of the point
    lon, lat = row['geometry'].x, row['geometry'].y
    
    # Get the tooltip text
    tooltip = f"Station: {row['LOCATION_N']} <br> Price: {row['mean sold price']}"
    
    # Create a marker for the point with tooltip
    marker = folium.CircleMarker(location=[lat, lon], radius = 4, color='black', fill_color = 'black', fill=True, tooltip=tooltip)
    
    # Add the marker to the feature group
#     marker.add_to(m2)
    marker.add_to(transit)
    
transit.add_to(m2)

# Add the feature group to the map
folium.LayerControl().add_to(m2)

m2

C:\Users\stdon\AppData\Local\Temp\ipykernel_12668\3430970625.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m2 = folium.Map(location=[hood_price_gdf.geometry.centroid.y.mean(), hood_price_gdf.geometry.centroid.x.mean()], zoom_start=11)


In [61]:
m2.save('C:/Users/stdon/Documents/Toronto-housing-price-prediction/opendata_neighbourhoods/price_map.html')

### Crime

In [60]:
# Create a Folium map centered on the mean of the GeoPandas DataFrame
## Reading this data file takes some time
crime_geodata = gpd.read_file('C:/Users/stdon/Documents/Toronto-housing-price-prediction/Major_Crime_Indicators_Open_Data/Major_Crime_Indicators_Open_Data.shp')
crime_geodata = crime_geodata.to_crs('EPSG:4326') ##consistent with neighbourhood data
crime_geodata.head()

OBJECTID      EVENT_UNIQ  REPORT_DAT    OCC_DATE  REPORT_YEA REPORT_MON  \
0         1  GO-20141262074  2014-01-01  1998-06-01        2014    January   
1         2  GO-20141260701  2014-01-01  2014-01-01        2014    January   
2         3  GO-20141260889  2014-01-01  2014-01-01        2014    January   
3         4  GO-20141260973  2014-01-01  2014-01-01        2014    January   
4         5  GO-20141261050  2014-01-01  2014-01-01        2014    January   

   REPORT_DAY  REPORT_DOY REPORT_DOW  REPORT_HOU  ...  UCR_EXT  \
0           1           1  Wednesday          12  ...      110   
1           1           1  Wednesday           3  ...      200   
2           1           1  Wednesday           4  ...      100   
3           1           1  Wednesday           4  ...      210   
4           1           1  Wednesday           4  ...      100   

                       OFFENCE       MCI_CATEGO  HOOD_158  \
0  Administering Noxious Thing          Assault        38   
1                          B&E  Break and Enter        70   
2                      Assault          Assault        74   
3                   Theft Over       Theft Over       NSA   
4                      Assault          Assault        69   

            NEIGHBOURH  HOOD_140                NEIGHBOU_1 LONG_WGS84  \
0     Lansing-Westgate        38     Lansing-Westgate (38) -79.425896   
1      South Riverdale        70      South Riverdale (70) -79.350229   
2  North St.James Town        74  North St.James Town (74) -79.376497   
3                  NSA       NSA                       NSA -85.488744   
4          Blake-Jones        66             Danforth (66) -79.344839   

   LAT_WGS84                    geometry  
0  43.757346  POINT (-79.42590 43.75735)  
1  43.646293  POINT (-79.35023 43.64629)  
2  43.666423  POINT (-79.37650 43.66642)  
3   0.000000   POINT (-85.48874 0.00000)  
4  43.678946  POINT (-79.34484 43.67895)  

[5 rows x 30 columns]

In [62]:
crime_5yr = crime_geodata[(crime_geodata['OCC_YEAR'] >= 2018) & (crime_geodata['OCC_YEAR'] <= 2022)]
crime_by_hood = crime_5yr.groupby(['HOOD_140'], as_index=False)['EVENT_UNIQ'].count()
crime_by_hood['Incidents 5yr Avg'] = round(crime_by_hood['EVENT_UNIQ']/5,0)
crime_by_hood.drop(columns='EVENT_UNIQ', inplace=True)
print(crime_by_hood.shape)
crime_by_hood.head()

### Check what are the categories of crime
# crime_geodata['OFFENCE'].value_counts(dropna=False)

(141, 2)


HOOD_140  Incidents 5yr Avg
0        1             1048.0
1       10               82.0
2      100              154.0
3      101              112.0
4      102              121.0

In [63]:
crime_by_hood= crime_by_hood.merge(hood_data[['Neighbourhood Number','Population, 2016']], how='inner', left_on='HOOD_140', right_on='Neighbourhood Number')
print(crime_by_hood.shape)

(140, 4)


In [64]:
crime_by_hood['crime chance (%)'] = round(crime_by_hood['Incidents 5yr Avg']/crime_by_hood['Population, 2016'].str.replace(',','').astype(int)*100,4)
crime_by_hood

HOOD_140  Incidents 5yr Avg Neighbourhood Number Population, 2016  \
0          1             1048.0                    1           33,312   
1         10               82.0                   10           11,051   
2        100              154.0                  100           11,817   
3        101              112.0                  101           10,732   
4        102              121.0                  102           12,806   
..       ...                ...                  ...              ...   
135       95              611.0                   95           30,526   
136       96              110.0                   96           10,968   
137       97               82.0                   97           12,528   
138       98              337.0                   98           20,923   
139       99              128.0                   99           16,775   

     crime chance (%)  
0              3.1460  
1              0.7420  
2              1.3032  
3              1.0436  
4              0.9449  
..                ...  
135            2.0016  
136            1.0029  
137            0.6545  
138            1.6107  
139            0.7630  

[140 rows x 5 columns]

In [65]:
crime_by_hood['HOOD_140'] = crime_by_hood['HOOD_140'].astype(int)

In [66]:
crime_hood_gdf = hood_geodata_map[['AREA_SHORT_CODE','AREA_NAME','geometry']].merge(crime_by_hood[['HOOD_140','Incidents 5yr Avg','crime chance (%)']],\
                                                                       how='left', left_on='AREA_SHORT_CODE', right_on='HOOD_140')



In [67]:

# m = folium.Map(location=[43.651, -79.347], zoom_start=10)
m3 = folium.Map(location=[hood_price_gdf.geometry.centroid.y.mean(), hood_price_gdf.geometry.centroid.x.mean()], zoom_start=11)

choropleth2 = folium.Choropleth(
    geo_data=crime_hood_gdf,
    name="crime rate",
    data=crime_hood_gdf,
    columns=['AREA_NAME','crime chance (%)'],
    key_on="feature.properties.AREA_NAME",
    fill_color="BuGn",
#     bins = [hood_price_gdf['soldPrice'].min(),800000, 900000,1000000,1100000, 1200000, 1500000, 2000000, \
#             hood_price_gdf['soldPrice'].max()],
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Crime Rate",
    highlight=True
).add_to(m3)

tooltip2 = folium.GeoJsonTooltip(
    fields=['AREA_NAME',"Incidents 5yr Avg",'crime chance (%)'],
    aliases=['Name:', 'Avg Yearly Incidents:','Chance of Crime:'],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """
)
# Add the tooltip to the choropleth map layer
choropleth2.geojson.add_child(tooltip2)


# # subway_colors = {'Sheppard Subway':'#B00085', 'Yonge-University-Spadina Subway':'#F3EB00',
# #        'Spadina Subway Extension':'#F3EB00', 'Eglinton Crosstown LRT':'#F39E00',
# #        'Eglinton West LRT':'#F39E00', 'Scarborough Subway':'#21A900', 'Finch West LRT':'#949793',
# #        'Bloor Subway':'#21A900', 'Ontario Line':'#009CD7'}

# transit = folium.FeatureGroup(name='transit',overlay=True,show=True)

# subway_line = folium.features.GeoJson(train_lines['geometry'], name='subway',
#                                         style_function = lambda x: {'color': 'black'
#                                                                     ,'weight': 5})
# # m3.add_child(subway_line)
# subway_line.add_to(transit)

# # for index, row in train_lines.iterrows():
# #     # Extract the LineString geometry
# #     curve = row['geometry']

# #     # Create a PolyLine and add it to the map
# #     if curve.type =='LineString':
# #         folium.PolyLine(locations=curve.coords, color='blue', weight=10).add_to(m3)
# #     else:
# #         for line in curve:
# #             folium.PolyLine(locations=line.coords, color='blue', weight=10).add_to(m3)
# # #     else:
# # #         print('not a line, cannot draw')

# # Iterate over the rows of the GeoDataFrame
# for index, row in train_stations_houses.iterrows():
#     # Get the coordinates of the point
#     lon, lat = row['geometry'].x, row['geometry'].y
    
#     # Get the tooltip text
#     tooltip = f"Station: {row['LOCATION_N']} <br> Price: {row['mean sold price']}"
    
#     # Create a marker for the point with tooltip
#     marker = folium.CircleMarker(location=[lat, lon], radius = 7, color='black', fill_color = 'black', fill=True, tooltip=tooltip)
    
#     # Add the marker to the feature group
# #     marker.add_to(m3)
#     marker.add_to(transit)
transit.show=False    
transit.add_to(m3)

# Add the feature group to the map
folium.LayerControl().add_to(m3)

m3

C:\Users\stdon\AppData\Local\Temp\ipykernel_12668\809629908.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m3 = folium.Map(location=[hood_price_gdf.geometry.centroid.y.mean(), hood_price_gdf.geometry.centroid.x.mean()], zoom_start=11)


In [33]:
m3.save('E:/Toronto-housing-price-prediction/Major_Crime_Indicators_Open_Data/crime_map.html')